In [17]:
import random
#Esta celda de codigo contiene la matriz inicial, las funciones para
#agregar GAPS, y crear la poblacion inicial 


#Matriz inicial
matriz_inicial = [
    'TGGTTGCGTTGCTTCTTCTGGCCATTTCGCATCTGTATAAC',
    'ATCAAAGATGAAATCTTCACCAAATGGCGCATTTTCTTCGATTTTATC',
    'TTGATTCTTTAGCATCTGGTTTAAATCCAACTACCACGGTTTG']
 

# Tamaño de la población inicial
tamano_poblacion = 10

# Población inicial
poblacion_inicial = []

#Funcion para insertar gaps de manera aleatoria
def agregar_gaps(secuencia):
    #Numero de gaps que se insertan
    num_gaps = 3
    for _ in range(num_gaps):
        #Posicion random de la secuencia
        posision = random.randint(0, len(secuencia))
        secuencia = secuencia[:posision] + '-' + secuencia[posision:]
    return secuencia

#Creamos la poblacion inicial en base a la matriz inicial
for _ in range(tamano_poblacion):
    # Elegimos aleatoriamente una secuencia de la lista de secuencias
    secuencia = random.choice(matriz_inicial)

    # Introducimos un "gap" en una posición aleatoria de la secuencia
    secuencia_gaps=agregar_gaps(secuencia)

    # Añadimos el individuo a la población inicial
    poblacion_inicial.append(secuencia_gaps)

#Imprimirmos la matriz inicial 

print("Matriz Inicial")
for i in(matriz_inicial):
    print(i)

#Se imprime la poblacion inicial que obtuvimos
print()
print("Poblacion inicial")
for i in(poblacion_inicial):
    print(i)
print()

Matriz Inicial
TGGTTGCGTTGCTTCTTCTGGCCATTTCGCATCTGTATAAC
ATCAAAGATGAAATCTTCACCAAATGGCGCATTTTCTTCGATTTTATC
TTGATTCTTTAGCATCTGGTTTAAATCCAACTACCACGGTTTG

Poblacion inicial
ATCAAA-GATGAAATC-TTCACCAAATGGCGCATTTTCTTCGATTTT-ATC
TGGTTG--CGT-TGCTTCTTCTGGCCATTTCGCATCTGTATAAC
TGGT-TGCGTTGCTTCTTCTGG--CCATTTCGCATCTGTATAAC
TTGATT-CTTTAGCATCT-GGTTTAAATCCA-ACTACCACGGTTTG
TGG-TTGCGT-TGCTTCTTCTGGCCATTTCGCATCTGTAT-AAC
TGGTTGCGTTGCTTCTTC-TGGC-CA-TTTCGCATCTGTATAAC
TTGATTCTTTAGCA-TCTGGTTTAAATCC-AACTACC-ACGGTTTG
ATCAAAGATGAAATCTTCAC-CAAATGGCGCATTTTCT-TCG-ATTTTATC
TGGTTGC-G-TTGCTTCTTCTGGCCATTTCGCATC-TGTATAAC
TGGTTGC-GTTGCTTCTTCTGGCCATTTCGCATCTGTATA-AC-



In [18]:

#Esta celda contiene las funciones que se usan para eliminar columnas de GAPS
#y la evaluacion de la poblacion 


#Funcion para eliminar columnas de gaps si es que existen
def eliminar_columnas_de_gaps(matriz):
    poblacion_transpuesta = list(map(list, zip(*matriz)))
    poblacion_transpuesta = [col for col in poblacion_transpuesta if any(c != '-' for c in col)]
    return list(map(''.join, zip(*poblacion_transpuesta)))


#SCORE para cada secuencia
#FUNCION PARA EVALUAR
def score_secuencias(secuencia, matriz):
    score = 0  # Inicializamos el puntaje

    # Eliminamos las columnas de gaps que existan
    nueva_poblacion = eliminar_columnas_de_gaps(matriz)

    # Recorremos cada columna de la matriz
    for i in range(len(nueva_poblacion[0])):

        columna = [fila[i] for fila in nueva_poblacion]

        gaps = columna.count('-')

        if secuencia[i] == '-':

            # Restamos 1 puntos por cada gap cuando hay gap en la misma posición            
            score -= gaps - 1
            # Restamos 2 puntos por cada gap cuando hay una letra en la misma posición
            score -= 2 * (len(columna) - gaps)

        else:

            # Sumamos 5 puntos por cada coincidencia y restamos 2 si no hay coincidencias
            score += 5 * (columna.count(secuencia[i]) - 1)
            score -= 2 * (len(nueva_poblacion) - columna.count(secuencia[i]))
            
    return score


In [19]:
#Celda 3 que contiene la seleccion de los padres y la
#particion de estos mismos 

#Funcion para seleccionar a los padres mejor calificados
def seleccionar_padres(poblacion):

    # Calificar todas las secuencias en la población
    calificaciones = [(secuencia, score_secuencias(secuencia, poblacion)) for secuencia in poblacion]

    # Ordenar las secuencias de mayor a menor calificación
    calificaciones.sort(key=lambda x: x[1], reverse=True)

    # Seleccionar las 2 secuencias más aptas
    padres = [secuencia for secuencia, calificacion in calificaciones[:2]]

    return padres


#Se ordenan de mayor a menos los score de la poblacion

def ordenar_secuencias(poblacion):

    # Calificar todas las secuencias en la población
    calificaciones = [(secuencia, score_secuencias(secuencia, poblacion)) for secuencia in poblacion]

    # Ordenar las secuencias de mayor a menor calificación
    calificaciones.sort(key=lambda x: x[1], reverse=True)

    for i in (calificaciones):
        print(i)

    # Devolver las secuencias ordenadas
    return [secuencia for secuencia, calificacion in calificaciones]


#Funcion para omitir los gaps en la division de los padres
def particion_padres(secuencia):

    partes = []
    parte_actual = ''
    contador = 0

    for caracter in secuencia:
        #condicion para saber si el caracter seleccionado es un GAP y no contarlo en la particion
        if caracter != '-':

            #Contador menor que 3 por que se diviran en 3 partes
            if contador < 3:
                parte_actual += caracter
                contador += 1
                
            #Se termina el "espacio" de la primera particion y continua
            if contador == 3:
                partes.append(parte_actual)
                parte_actual = ''
                contador = 0

        #Si es un GAP se agrega a la secuencia 
        else:
            parte_actual += caracter

    # Añadir la última parte si hay caracteres restantes
    if parte_actual:

        partes.append(parte_actual)

    return partes



In [20]:
#Celda que tiene la cruza de los padres, la creacion de los hijos
#y la sustitucion en la poblacion 

#Función para la cruza 
def cruzar(padre, madre):
    # Dividir las secuencias de los padres en partes válidas
    partes_padre = particion_padres(padre)

    partes_madre = particion_padres(madre)

    # Intercambiar las partes entre los padres para crear los hijos

    #El hijo 1 tiene partes exteriores del padre e interior de la madre
    hijo1 = ''.join(partes_padre[i] if i % 2 == 0 else partes_madre[i] for i in range(len(partes_padre)))

    #El hijo 2 contiene partes exteriores de la madre e interior del padre
    hijo2 = ''.join(partes_madre[i] if i % 2 == 0 else partes_padre[i] for i in range(len(partes_madre)))

    return hijo1, hijo2


#Agregar a los hijos a la poblacion y eliminar a los menos calificados
def sustuticion(poblacion, hijos):
    # Calificar todas las secuencias en la población
    calificaciones = [(secuencia, score_secuencias(secuencia, poblacion)) for secuencia in poblacion]

    # Ordenar las secuencias de mayor a menor calificación
    calificaciones.sort(key=lambda x: x[1], reverse=True)

    # Eliminar las 2 secuencias menos aptas
    poblacion = [secuencia for secuencia, calificacion in calificaciones[:-2]]
    
    #Se mutan a los hijos insertando mas gaps
    hijos_con_gaps = [agregar_gaps(hijo) for hijo in hijos]

    # Agregar los hijos a la población (ya mutados)

    poblacion.extend(hijos_con_gaps)

    return poblacion



In [21]:
#Celda qie contiene la funcion del algoritmo genetico, donde se juntan
#todas las funciones antes definidas

#Se crea la función "algoritmo_genetico" la cual junta todas las funciones
#para correrlo en un numero espefico de generaciones

def algoritmo_genetico(matriz_inicial, tamano_poblacion, num_generaciones):
    
    #Ciclo que realiza todas las generaciones que queramos
    for generacion in range(num_generaciones):
        
        #Se declara la nueva poblacion en cada generacion
        poblacion=poblacion_inicial
        print("------------------------------------")
        #Se imprime la nueva poblacion
        print("Nueva Poblacion")

        for i in(poblacion):
            print(i)
        print()
        
        #Se imprime el numero de la generacion en la que va
        print(f"Generación {generacion + 1}")

        #Se muestran las secuencias ordenadas junto con su puntaje
        print("Secuencias ordenadas por calificacion")

        poblacion_ordenada = ordenar_secuencias(poblacion)
        print()

        #Se imprimen los padres que se han elegido en esta generacion
        print("Padres Seleccionados")
        padres = seleccionar_padres(poblacion)
        for i in(padres):
            print(i)
        print()

        #Los hijos tambien se imprimen
        hijo1, hijo2 = cruzar(padres[0], padres[1])
        print("Hijos")
        print("Hijo 1: ",hijo1)
        print("Hijo 2: ",hijo2)
        print()

        #Se sustituyen en la nueva poblacion y se imprime
        poblacion = sustuticion(poblacion, [hijo1, hijo2])
        print("Nueva poblacion")
        for secuencia in poblacion:
            print(secuencia)
        print()


# Ejecutar el algoritmo genético
num_generaciones = 2000  # Número de generaciones que se desea ejecutar
#Se muestra todo el algoritmo 
algoritmo_genetico(matriz_inicial, tamano_poblacion, num_generaciones)


------------------------------------
Nueva Poblacion
ATCAAA-GATGAAATC-TTCACCAAATGGCGCATTTTCTTCGATTTT-ATC
TGGTTG--CGT-TGCTTCTTCTGGCCATTTCGCATCTGTATAAC
TGGT-TGCGTTGCTTCTTCTGG--CCATTTCGCATCTGTATAAC
TTGATT-CTTTAGCATCT-GGTTTAAATCCA-ACTACCACGGTTTG
TGG-TTGCGT-TGCTTCTTCTGGCCATTTCGCATCTGTAT-AAC
TGGTTGCGTTGCTTCTTC-TGGC-CA-TTTCGCATCTGTATAAC
TTGATTCTTTAGCA-TCTGGTTTAAATCC-AACTACC-ACGGTTTG
ATCAAAGATGAAATCTTCAC-CAAATGGCGCATTTTCT-TCG-ATTTTATC
TGGTTGC-G-TTGCTTCTTCTGGCCATTTCGCATC-TGTATAAC
TGGTTGC-GTTGCTTCTTCTGGCCATTTCGCATCTGTATA-AC-

Generación 1
Secuencias ordenadas por calificacion
('TGGTTGC-G-TTGCTTCTTCTGGCCATTTCGCATC-TGTATAAC', 288)
('TGGTTGCGTTGCTTCTTC-TGGC-CA-TTTCGCATCTGTATAAC', 267)
('TGGT-TGCGTTGCTTCTTCTGG--CCATTTCGCATCTGTATAAC', 259)
('TGG-TTGCGT-TGCTTCTTCTGGCCATTTCGCATCTGTAT-AAC', 189)
('TGGTTGC-GTTGCTTCTTCTGGCCATTTCGCATCTGTATA-AC-', 177)
('TGGTTG--CGT-TGCTTCTTCTGGCCATTTCGCATCTGTATAAC', 157)
('TTGATT-CTTTAGCATCT-GGTTTAAATCCA-ACTACCACGGTTTG', 44)
('TTGATTCTTTAGCA-TCTGGTTTAAATCC-AACTACC-ACGGTTTG